In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!unzip -q '/content/drive/My Drive/YOLO_Data/combined_dataset.zip' -d /content/Dataset


In [ ]:
import os
import shutil
from pathlib import Path

# Recursive Merge Picture Functions
def flatten_image_dir(root_dir):
    root = Path(root_dir)
    for subdir, _, files in os.walk(root):
        for file in files:
            if file.endswith(".jpg"):
                src = Path(subdir) / file
                dst = root / file
                # Avoid overwriting renamed files
                if dst.exists():
                    dst = root / f"{src.stem}_{hash(src)}.jpg"
                shutil.move(str(src), str(dst))

    # Delete subsets
    for folder in root.glob("*/"):
        if folder.is_dir():
            shutil.rmtree(folder)

# Process train and val
flatten_image_dir("/content/Dataset/combined_dataset/images/train")
flatten_image_dir("/content/Dataset/combined_dataset/images/val")


In [ ]:
import os
import pandas as pd

def convert_csv_to_yolo(csv_path, image_dir, label_dir, image_size=(640, 480), class_id=1):
    os.makedirs(label_dir, exist_ok=True)
    df = pd.read_csv(csv_path)

    for _, row in df.iterrows():
        image_name = row['filename']
        width = row['width']
        height = row['height']
        xmin = row['xmin']
        ymin = row['ymin']
        xmax = row['xmax']
        ymax = row['ymax']

        # YOLO format: x_center, y_center, w, h (all normalized)
        x_center = (xmin + xmax) / 2 / width
        y_center = (ymin + ymax) / 2 / height
        w = (xmax - xmin) / width
        h = (ymax - ymin) / height

        yolo_line = f"{class_id} {x_center:.6f} {y_center:.6f} {w:.6f} {h:.6f}"

        # write to label file
        label_filename = os.path.splitext(image_name)[0] + ".txt"
        label_path = os.path.join(label_dir, label_filename)

        with open(label_path, "a") as f:
            f.write(yolo_line + "\n")

    print(f"Converted {csv_path} to YOLO labels in {label_dir}")


if __name__ == "__main__":
    #Train
    train_csv = "/content/Dataset/combined_dataset/labels/train/license_plate_train_annotations.csv"
    train_images = "/content/Dataset/combined_dataset/images/train"
    train_labels = "/content/Dataset/combined_dataset/labels/train"
    convert_csv_to_yolo(train_csv, train_images, train_labels)


    # Val
    val_csv = "/content/Dataset/combined_dataset/labels/val/license_plate_val_annotations.csv"
    val_images = "/content/Dataset/combined_dataset/images/val"
    val_labels = "/content/Dataset/combined_dataset/labels/val"
    convert_csv_to_yolo(val_csv, val_images, val_labels)


Converted /content/Dataset/combined_dataset/labels/train/license_plate_train_annotations.csv to YOLO labels in /content/Dataset/combined_dataset/labels/train
Converted /content/Dataset/combined_dataset/labels/val/license_plate_val_annotations.csv to YOLO labels in /content/Dataset/combined_dataset/labels/val


In [ ]:
import os

def parse_wider_txt(txt_path, image_dir, label_dir, image_size=(640, 480), class_id=0):
    os.makedirs(label_dir, exist_ok=True)

    with open(txt_path, 'r') as f:
        lines = f.readlines()

    idx = 0
    while idx < len(lines):
        filename = lines[idx].strip()
        idx += 1

        if idx >= len(lines):
            break

        face_count_line = lines[idx].strip()
        if not face_count_line.isdigit():
            print(f"[Warning] Invalid face count '{face_count_line}' at line {idx}, filename: {filename}")
            idx += 1
            continue

        face_count = int(face_count_line)
        idx += 1
        label_lines = []

        for _ in range(face_count):
            if idx >= len(lines):
                break
            parts = lines[idx].strip().split()
            if len(parts) < 4:
                idx += 1
                continue
            try:
                x, y, w, h = map(float, parts[:4])
            except ValueError:
                print(f"[Warning] Invalid box format at line {idx}: {parts}")
                idx += 1
                continue

            # Convert to YOLO format (normalized center x, center y, width, height)
            x_center = (x + w / 2) / image_size[0]
            y_center = (y + h / 2) / image_size[1]
            w_norm = w / image_size[0]
            h_norm = h / image_size[1]

            label_line = f"{class_id} {x_center:.6f} {y_center:.6f} {w_norm:.6f} {h_norm:.6f}"
            label_lines.append(label_line)
            idx += 1

        # Save to label file
        base_name = os.path.splitext(os.path.basename(filename))[0]
        label_path = os.path.join(label_dir, base_name + ".txt")

        if label_lines:
            with open(label_path, 'w') as lf:
                lf.write('\n'.join(label_lines))
            print(f"[Info] Saved {len(label_lines)} labels to {label_path}")
        else:
            print(f"[Skip] No valid faces for {filename}, skipping file.")

    print(f"[Done] Finished parsing {txt_path} to YOLO format at {label_dir}")



#Start conversion
parse_wider_txt(
    txt_path="/content/Dataset/combined_dataset/labels/train/wider_face_train_bbx_gt.txt",
    image_dir="/content/Dataset/combined_dataset/images/train",
    label_dir="/content/Dataset/combined_dataset/labels/train",
    class_id=0
)

parse_wider_txt(
    txt_path="/content/Dataset/combined_dataset/labels/val/wider_face_val_bbx_gt.txt",
    image_dir="/content/Dataset/combined_dataset/images/val",
    label_dir="/content/Dataset/combined_dataset/labels/val",
    class_id=0
)


Streaming output truncated to the last 5000 lines.
[Info] Saved 1 labels to /content/Dataset/combined_dataset/labels/train/55_Sports_Coach_Trainer_sportcoaching_55_753.txt
[Info] Saved 2 labels to /content/Dataset/combined_dataset/labels/train/55_Sports_Coach_Trainer_sportcoaching_55_327.txt
[Info] Saved 2 labels to /content/Dataset/combined_dataset/labels/train/55_Sports_Coach_Trainer_sportcoaching_55_473.txt
[Info] Saved 2 labels to /content/Dataset/combined_dataset/labels/train/55_Sports_Coach_Trainer_sportcoaching_55_914.txt
[Info] Saved 4 labels to /content/Dataset/combined_dataset/labels/train/55_Sports_Coach_Trainer_sportcoaching_55_596.txt
[Info] Saved 3 labels to /content/Dataset/combined_dataset/labels/train/55_Sports_Coach_Trainer_sportcoaching_55_387.txt
[Info] Saved 35 labels to /content/Dataset/combined_dataset/labels/train/55_Sports_Coach_Trainer_sportcoaching_55_877.txt
[Info] Saved 4 labels to /content/Dataset/combined_dataset/labels/train/55_Sports_Coach_Trainer_sport

In [ ]:
import os

val_label_dir = "/content/Dataset/combined_dataset/labels/val"

# 1. 列出 .txt 文件数量
txt_files = [f for f in os.listdir(val_label_dir) if f.endswith(".txt")]
print(f"标签文件数量: {len(txt_files)}")

# 2. 检查是否有空文件
empty_files = [f for f in txt_files if os.path.getsize(os.path.join(val_label_dir, f)) == 0]
print(f"空标签文件数量: {len(empty_files)}")


标签文件数量: 5272
空标签文件数量: 0


In [ ]:
!pip install ultralytics -U

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 42.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 1.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 68.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 51.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 37.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 7.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 14.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 42.4 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstalling 

In [ ]:
from ultralytics import YOLO
model = YOLO("yolov8n.yaml")
model.train(data="/content/Dataset/combined_data.yaml", epochs=50, imgsz=640, batch=16)


Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.
Ultralytics 8.3.167 🚀 Python-3.11.13 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
engine/trainer: agnostic_nms=False, amp=True, augment=False, auto_augment=randaugment, batch=16, bgr=0.0, box=7.5, cache=False, cfg=None, classes=None, close_mosaic=10, cls=0.5, conf=None, copy_paste=0.0, copy_paste_mode=flip, cos_lr=False, cutmix=0.0, data=/content/Dataset/combined_data.yaml, degrees=0.0, deterministic=True, device=None, dfl=1.5, dnn=False, dropout=0.0, dynamic=False, embed=None, epochs=50, erasing=0.4, exist_ok=False, fliplr=0.5, flipud=0.0, format=torchscript, fraction=1.0, freeze=None, half=False, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, imgsz=640, int8=False, iou=0.7, keras=False, ko

100%|██████████| 755k/755k [00:00<00:00, 107MB/s]

Overriding model.yaml nc=80 with nc=2

                   from  n    params  module                                       arguments                     
  0                  -1  1       464  ultralytics.nn.modules.conv.Conv             [3, 16, 3, 2]                 
  1                  -1  1      4672  ultralytics.nn.modules.conv.Conv             [16, 32, 3, 2]                
  2                  -1  1      7360  ultralytics.nn.modules.block.C2f             [32, 32, 1, True]             
  3                  -1  1     18560  ultralytics.nn.modules.conv.Conv             [32, 64, 3, 2]                
  4                  -1  2     49664  ultralytics.nn.modules.block.C2f             [64, 64, 2, True]             
  5                  -1  1     73984  ultralytics.nn.modules.conv.Conv             [64, 128, 3, 2]               
  6                  -1  2    197632  ultralytics.nn.modules.block.C2f             [128, 128, 2, True]           
  7                  -1  1    295424  ultralytics

YOLOv8n summary: 129 layers, 3,011,238 parameters, 3,011,222 gradients, 8.2 GFLOPs

Freezing layer 'model.22.dfl.conv.weight'
AMP: running Automatic Mixed Precision (AMP) checks...


100%|██████████| 5.35M/5.35M [00:00<00:00, 175MB/s]


...

      48/50      3.45G       1.31      1.068       1.55          3        640: 100%|██████████| 699/699 [03:59<00:00,  2.92it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 96/96 [00:28<00:00,  3.33it/s]


                   all       3043       3726      0.617       0.54      0.533       0.37

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


      49/50      3.48G      1.309      1.059      1.543          3        640: 100%|██████████| 699/699 [03:55<00:00,  2.97it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 96/96 [00:27<00:00,  3.45it/s]


                   all       3043       3726       0.62      0.538      0.534      0.369

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


      50/50      3.48G      1.307      1.062      1.547         17        640:  99%|█████████▊| 689/699 [03:53<00:03,  3.21it/s]

In [ ]:
!zip -r runs_train_results.zip runs/
